# Extracting Fit Fractions

A fit results file (read in using AmpTools.FitResults) is dumped after an AmpTools fit is completed. These fit results can be parsed to extract the intensity (or fit fraction) of each amplitude. A typical procedure is to parse the fit results and dump the fit fractions for each unique amplitude and for **user specified coherent sums**. 

Each **AmpTools** amplitude name takes the form `REACTION::SUM::AMPLITUDE`. Everyone has their own naming schemes so a flexible way to form coherent sums is needed.

`pa fitfrac` takes a flag `--regex_merge` which allows a user to specify a substitution pattern to merge amplitudes

An additional flag `--test_regex` can be used to test the regex pattern without calling AmpTools to return the intensity and is used everywhere in this tutorial.

## Docstring: `pa fitfrac`

In [14]:
import os
from pyamptools.extract_ff import extract_ff

PYAMPTOOLS_HOME = os.environ["PYAMPTOOLS_HOME"]
SRC = f"{PYAMPTOOLS_HOME}/src/pyamptools"
fit_results = f"{PYAMPTOOLS_HOME}/tests/samples/SIMPLE_EXAMPLE/result.fit"
output_file = f"{PYAMPTOOLS_HOME}/tests/ff.txt"

help(extract_ff)

Help on function extract_ff in module pyamptools.extract_ff:

extract_ff(results, outfileName='', fmt='.5f', test_regex=False, no_phases=False, only=None, regex_merge=None)
    Extract fit fractions and phase differences between pairs of waves from a FitResults object.
    
    Args:
        results (FitResults): FitResults object containing fit results
        outfileName (str): Output root file name or dump to stdout if empty string
        fmt (str): String format for printing numbers
        test_regex (bool, optional): If True, only test and print regex grouping without calculating intensities
        no_phases (bool, optional): If True, skip calculating phase differences
        only (str, optional): Only dump fit fractions for "acc" or "noacc". Default dumps both.
        regex_merge (List[str], optional): List of regex pattern/replace pairs for merging amplitudes.
            Pairs are separated by ~>. The substitution happens for all amplitude names.
            All amplitudes

```{note}
`--regex_merge` takes at least one substitution pattern. Multiple patterns can be passed, i.e. the following two examples can be combined to produce two sets of coherent sums: `--regex_merge ".*::(.*)::.*~>\\1" ".*::.*::"`
```

## Example 1

In this fit results file we have several amplitudes: 

```
etapi::reZ::resAmp1
etapi::imZ::resAmp1
etapi::reZ::resAmp2
etapi::imZ::resAmp2
etapi::reZ::resAmp3
etapi::imZ::resAmp3
```

What if we wanted to calculate intensity for the coherent sums across all amplitudes that share the same SUM

`'.*::(.*)::.*~>\\1'` will match the form of our amplitude names, capture the SUM, and replace the match with the SUM. `~>` is our delimiter that separates the pattern from its replacement. In this case etapi::reZ::resAmp1 and etapi::reZ::resAmp2 will both reduce to reZ. Amplitudes with same reduced name will be put into a list which will be passed to `AmpTools.FitResults.intensity()`.

In [15]:
cmd = [
    "pa fitfrac",
    fit_results,
    "--outputfileName",
    output_file,
    "--test_regex",
    "--regex_merge",
    "'.*::(.*)::.*~>\\1'"
]
cmd = " ".join(cmd)
print(cmd)
os.system(cmd)

pa fitfrac /w/halld-scshelf2101/lng/WORK/PyAmpTools9/tests/samples/SIMPLE_EXAMPLE/result.fit --outputfileName /w/halld-scshelf2101/lng/WORK/PyAmpTools9/tests/ff.txt --test_regex --regex_merge '.*::(.*)::.*~>\1'
atiSetup| pa called python

------------------------------------------------
atiSetup| MPI is disabled
atiSetup| GPU is disabled
------------------------------------------------


atiSetup| Loading library libIUAmpTools.so ............  ON
atiSetup| Loading library libAmpTools.so ..............  ON
atiSetup| Loading library libAmpPlotter.so ............  ON
atiSetup| Loading library libAmpsDataIO.so ............  ON
atiSetup| Loading library libFSRoot.so ................  OFF
atiSetup| Loading library libAmpsGen.so ...............  OFF


------------------------------------------------
------------------------------------------------

   |        ^                                                      |
   |       / \             Version:  v0.15.3-2-g0753-dirty         |
   |    

0

## Example 2

What if we wanted to calculate intensity for the coherent sums: {resAmp1, resAmp2, resAmp3} summing over reaction and sum? 

`'.*::.*::'` will pattern match the REACTION::SUM part of the amplitude name. Since there is no replacement (i.e. no `~>`) this acts like a substitution with an empty string (or deletion...). In this case etapi::reZ::resAmp1 and etapi::imZ::resAmp1 will both reduce to resAmp1. Amplitudes with same reduced name will be put into a list which will be passed to `AmpTools.FitResults.intensity()`.

In [16]:
cmd = [
    "pa fitfrac",
    fit_results,
    "--outputfileName",
    output_file,
    "--test_regex",
    "--regex_merge",
    "'.*::.*::'"
]
cmd = " ".join(cmd)
print(cmd)
os.system(cmd)

pa fitfrac /w/halld-scshelf2101/lng/WORK/PyAmpTools9/tests/samples/SIMPLE_EXAMPLE/result.fit --outputfileName /w/halld-scshelf2101/lng/WORK/PyAmpTools9/tests/ff.txt --test_regex --regex_merge '.*::.*::'
atiSetup| pa called python

------------------------------------------------
atiSetup| MPI is disabled
atiSetup| GPU is disabled
------------------------------------------------


atiSetup| Loading library libIUAmpTools.so ............  ON
atiSetup| Loading library libAmpTools.so ..............  ON
atiSetup| Loading library libAmpPlotter.so ............  ON
atiSetup| Loading library libAmpsDataIO.so ............  ON
atiSetup| Loading library libFSRoot.so ................  OFF
atiSetup| Loading library libAmpsGen.so ...............  OFF


------------------------------------------------
------------------------------------------------

   |        ^                                                      |
   |       / \             Version:  v0.15.3-2-g0753-dirty         |
   |      /---\ 

0